In [1]:
import pandas as pd
import numpy as np
import openpyxl
import os.path
from save2Excel import save2Excel

/mnt/7ACA0CC0CA0C7B21/temp/py36/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


In [2]:
# loading the file
df = pd.read_csv('TSRTC-alldepots-ORIG.csv', dtype=str).fillna('')

In [3]:
print(df.shape)
df.columns

(437060, 28)


Index(['DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER', 'TRIP_ID',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME', 'STAGE_TYPE',
       'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'TO_TIME', 'BREAK_TIME',
       'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE', 'OD_WED', 'OD_THU', 'OD_FRI',
       'OD_SAT', 'OD_SUN', 'DATA_ORDR'],
      dtype='object')

# lets make routes
check route ids and names for combined uniqueness

In [4]:
routesDF = df[['ROUTE_ID','ROUTE_NUMBER','DEPOT_CODE']].drop_duplicates('ROUTE_ID').sort_values(['ROUTE_NUMBER','ROUTE_ID'])
routesDF

ROUTE_ID    ROUTE_NUMBER DEPOT_CODE
68523     16390                        CCL
184288    15296         212/568        HPT
217537       77               1        KCG
366717     8026              10        RN1
95178      7471             100        DSR
250390    24589            100D        MDN
5108       6335            100R        BGD
251067    28949          101K/D        MDN
251772     6008             102        MDN
276646    11905        102/253L        MHM
258996     6036          102A/G        MDN
250614     5922            102B        MDN
266715     5924       102B/218L        MDN
250913     6026            102C        MDN
111402    14499            102K        FNR
251928     6015            102K        MDN
256391     6018            102M        MDN
271574     6048            102P        MDN
256144     6047            102W        MDN
259897     6032             103        MDN
251171     6014            104A        MDN
258062     5946        104A/216        MDN
269795     5948       104M/127K        MDN
258756     6011            104R        MDN
268543     5982       104R/127K        MDN
262803     5923       104R/218L        MDN
256937     5945            104S        MDN
258504     6038             105        MDN
182960     9360         107J/21        HPT
74217      5288           107JD        CNT
...         ...             ...        ...
221064     9947          KADAPA        KCG
41412     27009             KNL        BHL
247824    18909              KP        KPL
394851    29219              M1        RN2
97052      9648      MARKAPURAM        DSR
435907    11786   MGBS-TIRUPATI        UPL
340536    12272          MP-NZB        MPM
295887    15396         MYP-GDK        MI1
295983    15397        MYP-KRMR        MI1
279173    10022         MYP-NZB        MI1
279033     9827         MYP-VJA        MI1
279493    10023        MYP-WGLL        MI1
48243      9825             NDL        BKP
340488    11047  NIZAMABAD-ARSP        MPM
340440    11049  NIZAMABAD-MBRK        MPM
97028      9647          ONGOLE        DSR
315032    10841              P1        MI2
48463     14250      PALAMANERU        BKP
91376      7427            PCPL        DSR
41120     11608     PULIVENDULA        BHL
343836    12478     THADIPATHRI        MS1
96992      9646      VIJAYAWADA        DSR
172484    10027             VJA        HN2
24427      9780             VJA        BHL
250082     9997             VJA        KPL
278465     9831        VJA-ATNR        MI1
341264    11014        WARANGAL        MPM
341456    11027   WARANGAL-BMRM        MPM
341312    11026    WARANGAL-PCM        MPM
416031     6601             YGT        UPL

[833 rows x 3 columns]

In [5]:
len(routesDF)

833

In [7]:
len(routesDF.ROUTE_NUMBER.unique())

696

### 833 routes

In [8]:
print(routesDF.ROUTE_NUMBER.unique().tolist())

['', ' 212/568', '1', '10', '100', '100D', '100R', '101K/D', '102', '102/253L', '102A/G', '102B', '102B/218L', '102C', '102K', '102M', '102P', '102W', '103', '104A', '104A/216', '104M/127K', '104R', '104R/127K', '104R/218L', '104S', '105', '107J/21', '107JD', '107JS', '107JS-XC', '107V/R', '107VR', '107VR-ME', '107VR-SN', '10A/S', '10AS', '10BK', '10F', '10F/V', '10H', '10H/16A', '10H/25I', '10H/L', '10HA', '10K', '10K/L', '10K/P', '10KB', '10KJ', '10KM', '10L', '10L/18', '10Y/F', '10YF', '10YH', '113A', '113E/L', '113F', '113I/KP', '113I/M', '113I/V', '113K', '113K/225L', '113K/L', '113M', '113M/216', '113M/288', '113M/W', '113MG', '113Y', '113Y/K', '113YK', '115', '115C', '115M', '116', '116N', '116P', '117', '117L', '118D', '118G', '118H', '118P', '118W', '11W', '120', '120K', '120M', '123', '126/300', '126M', '127K', '127K/V', '127S', '127k', '136H', '136N', '142N', '147', '14X', '156', '156/118', '156/126', '156/216G', '156/288', '156/299', '156B/118', '156L', '156V', '158/277D', 

### checking if in this id-name list, is the id ever repeating?

In [9]:
idDupes = routesDF.ROUTE_ID.duplicated()
idDupes[(idDupes == True)]

Series([], Name: ROUTE_ID, dtype: bool)

### > nope, id's are unique. 
Remaining grouping etc we can do after making gtfs routes.txt


## blanks:

In [10]:
# cross-check that.. because further below it ain't coming so.
routesDF[ (routesDF.ROUTE_NUMBER == '') ]

ROUTE_ID ROUTE_NUMBER DEPOT_CODE
68523    16390                     CCL

### > ROUTE_ID 16390 has blank ROUTE_NUMBER.
Will have to mark this for now.

In [11]:
routesDF.ROUTE_NUMBER.replace('','BLANK',inplace=True)

In [12]:
routesDF[ (routesDF.ROUTE_NUMBER == 'BLANK') ]

ROUTE_ID ROUTE_NUMBER DEPOT_CODE
68523    16390        BLANK        CCL

## data cleaning
leading, trailing blanks

In [13]:
# first, find them
routesDF[ routesDF.ROUTE_NUMBER != routesDF.ROUTE_NUMBER.str.strip() ]

ROUTE_ID ROUTE_NUMBER DEPOT_CODE
184288    15296      212/568        HPT

In [14]:
# then, clean them
routesDF.ROUTE_NUMBER = routesDF.ROUTE_NUMBER.apply(lambda x: x.strip())

In [15]:
# check again
print( routesDF[ routesDF.ROUTE_NUMBER != routesDF.ROUTE_NUMBER.str.strip() ] )

Empty DataFrame
Columns: [ROUTE_ID, ROUTE_NUMBER, DEPOT_CODE]
Index: []


In [16]:
'#'*100

'####################################################################################################'

## sort routesDF
Have to sort it such that 2,2J,2AB etc come in the same series, then 3 comes and not 21. So, direct sorting of the route_number column won't work as they're all strings.

Get the number part of ROUTE_NUMBER so we can sort it by that.

In [17]:
def parse_int(x):
    ''' 
    from https://gist.github.com/lsauer/6088767#gistcomment-2309011
    take just the initial numeric digits of a string and convert to number
    '''
    temp = []
    for c in str(x).strip():
        if c.isdigit():
            temp.append(c)
        else:
            break
    return int("".join(temp)) if "".join(temp) else ''

In [18]:
routesDF['number_part'] = routesDF.ROUTE_NUMBER.apply(parse_int)

In [19]:
routesDF.sort_values(['number_part','ROUTE_NUMBER','DEPOT_CODE','ROUTE_ID'], inplace=True)

In [20]:
routesDF

ROUTE_ID    ROUTE_NUMBER DEPOT_CODE number_part
217537       77               1        KCG           1
219172    14221              1B        KCG           1
91665      7468              1D        DSR           1
143173     5899          1D/299        HN1           1
155639    10036         1D/299S        HN2           1
984       14955            1D/J        BGD           1
133282     5928            1D/V        HN1           1
217651      138              1J        KCG           1
5352       6360              1L        BGD           1
1658       6331            1M/D        BGD           1
219400       78              1P        KCG           1
184358     9358          1P/25S        HPT           1
156215     6082              1V        HN2           1
341753      658              1Z        MS1           1
70729      5291              2C        CNT           2
109972    14054              2C        FNR           2
216829      115              2J        KCG           2
110957    14497              2U        FNR           2
354256     5493              2Z        RJN           2
103084     5607               3        FMA           3
225011    10154              3D        KGD           3
225621    10161              3H        KGD           3
341965      574            3H/N        MS1           3
221292    10110             3HN        KGD           3
217341       17              3K        KCG           3
229542    10109              3K        KGD           3
343135      575              3K        MS1           3
344024     5595              3K        MS2           3
243364    11913          3K/252        KGD           3
65688      9436             3KL        CCL           3
...         ...             ...        ...         ...
221064     9947          KADAPA        KCG            
41412     27009             KNL        BHL            
247824    18909              KP        KPL            
394851    29219              M1        RN2            
97052      9648      MARKAPURAM        DSR            
435907    11786   MGBS-TIRUPATI        UPL            
340536    12272          MP-NZB        MPM            
295887    15396         MYP-GDK        MI1            
295983    15397        MYP-KRMR        MI1            
279173    10022         MYP-NZB        MI1            
279033     9827         MYP-VJA        MI1            
279493    10023        MYP-WGLL        MI1            
48243      9825             NDL        BKP            
340488    11047  NIZAMABAD-ARSP        MPM            
340440    11049  NIZAMABAD-MBRK        MPM            
97028      9647          ONGOLE        DSR            
315032    10841              P1        MI2            
48463     14250      PALAMANERU        BKP            
91376      7427            PCPL        DSR            
41120     11608     PULIVENDULA        BHL            
343836    12478     THADIPATHRI        MS1            
96992      9646      VIJAYAWADA        DSR            
24427      9780             VJA        BHL            
172484    10027             VJA        HN2            
250082     9997             VJA        KPL            
278465     9831        VJA-ATNR        MI1            
341264    11014        WARANGAL        MPM            
341456    11027   WARANGAL-BMRM        MPM            
341312    11026    WARANGAL-PCM        MPM            
416031     6601             YGT        UPL            

[833 rows x 4 columns]

In [21]:
'#'*100

'####################################################################################################'

# create gtfs routes.txt
https://github.com/google/transit/blob/master/gtfs/spec/en/reference.md#routestxt
required fields: route_id route_short_name route_long_name route_type (3-bus) 

In [22]:
gtfsroutes = routesDF[['ROUTE_ID','ROUTE_NUMBER']].rename(columns={'ROUTE_ID':'route_id','ROUTE_NUMBER':'route_short_name'})
gtfsroutes['route_long_name'] = routesDF['DEPOT_CODE'] + ' depot, route: ' + routesDF['ROUTE_NUMBER']
gtfsroutes['route_type'] = 3
gtfsroutes['agency_id'] = 'TSRTC_HYD' # from agency.txt, refer there for exact
gtfsroutes

route_id route_short_name                   route_long_name  \
217537       77                1               KCG depot, route: 1   
219172    14221               1B              KCG depot, route: 1B   
91665      7468               1D              DSR depot, route: 1D   
143173     5899           1D/299          HN1 depot, route: 1D/299   
155639    10036          1D/299S         HN2 depot, route: 1D/299S   
984       14955             1D/J            BGD depot, route: 1D/J   
133282     5928             1D/V            HN1 depot, route: 1D/V   
217651      138               1J              KCG depot, route: 1J   
5352       6360               1L              BGD depot, route: 1L   
1658       6331             1M/D            BGD depot, route: 1M/D   
219400       78               1P              KCG depot, route: 1P   
184358     9358           1P/25S          HPT depot, route: 1P/25S   
156215     6082               1V              HN2 depot, route: 1V   
341753      658               1Z              MS1 depot, route: 1Z   
70729      5291               2C              CNT depot, route: 2C   
109972    14054               2C              FNR depot, route: 2C   
216829      115               2J              KCG depot, route: 2J   
110957    14497               2U              FNR depot, route: 2U   
354256     5493               2Z              RJN depot, route: 2Z   
103084     5607                3               FMA depot, route: 3   
225011    10154               3D              KGD depot, route: 3D   
225621    10161               3H              KGD depot, route: 3H   
341965      574             3H/N            MS1 depot, route: 3H/N   
221292    10110              3HN             KGD depot, route: 3HN   
217341       17               3K              KCG depot, route: 3K   
229542    10109               3K              KGD depot, route: 3K   
343135      575               3K              MS1 depot, route: 3K   
344024     5595               3K              MS2 depot, route: 3K   
243364    11913           3K/252          KGD depot, route: 3K/252   
65688      9436              3KL             CCL depot, route: 3KL   
...         ...              ...                               ...   
221064     9947           KADAPA          KCG depot, route: KADAPA   
41412     27009              KNL             BHL depot, route: KNL   
247824    18909               KP              KPL depot, route: KP   
394851    29219               M1              RN2 depot, route: M1   
97052      9648       MARKAPURAM      DSR depot, route: MARKAPURAM   
435907    11786    MGBS-TIRUPATI   UPL depot, route: MGBS-TIRUPATI   
340536    12272           MP-NZB          MPM depot, route: MP-NZB   
295887    15396          MYP-GDK         MI1 depot, route: MYP-GDK   
295983    15397         MYP-KRMR        MI1 depot, route: MYP-KRMR   
279173    10022          MYP-NZB         MI1 depot, route: MYP-NZB   
279033     9827          MYP-VJA         MI1 depot, route: MYP-VJA   
279493    10023         MYP-WGLL        MI1 depot, route: MYP-WGLL   
48243      9825              NDL             BKP depot, route: NDL   
340488    11047   NIZAMABAD-ARSP  MPM depot, route: NIZAMABAD-ARSP   
340440    11049   NIZAMABAD-MBRK  MPM depot, route: NIZAMABAD-MBRK   
97028      9647           ONGOLE          DSR depot, route: ONGOLE   
315032    10841               P1              MI2 depot, route: P1   
48463     14250       PALAMANERU      BKP depot, route: PALAMANERU   
91376      7427             PCPL            DSR depot, route: PCPL   
41120     11608      PULIVENDULA     BHL depot, route: PULIVENDULA   
343836    12478      THADIPATHRI     MS1 depot, route: THADIPATHRI   
96992      9646       VIJAYAWADA      DSR depot, route: VIJAYAWADA   
24427      9780              VJA             BHL depot, route: VJA   
172484    10027              VJA             HN2 depot, route: VJA   
250082     9997              VJA             KPL depot, route: VJA   
278465     9831  

In [23]:
gtfsroutes.to_csv('routes.txt',index=False)

### > done creating routes.txt

In [24]:
'#'*100

'####################################################################################################'

# Analyis

## check if ROUTE_NUMBER is repeating 

In [25]:
nameCount = routesDF.groupby(['ROUTE_NUMBER']).ROUTE_NUMBER.count()
nameCount[nameCount > 1]

ROUTE_NUMBER
102K       2
107V/R     3
10F        2
10H        2
10K        2
10KM       2
10L/18     2
113A       2
113K/L     3
113M       4
113M/W     2
115        2
115M       2
116N       2
11W        2
127K       3
127K/V     2
147        2
156/299    2
156L       2
156V       2
158F       2
16C        2
171        2
17D        2
17H/10W    2
187D/V     2
187P       2
189M       2
195W       3
          ..
455        2
458        2
45F        2
478        2
47L        2
49M        2
49M/250    2
532        2
568        2
5G         2
5K         2
63M        2
65G        2
66G        2
6NG        2
72H        2
72V        2
7Z         2
83J        2
8A         3
8A/U       2
8C         2
8M         2
90L        5
95M        2
9F         2
9K         2
9X         4
GUNTUR     2
VJA        3
Name: ROUTE_NUMBER, Length: 97, dtype: int64

### > yes, ROUTE_NUMBER values are repeating in 97 cases.

In [26]:
# example: 107V/R
routesDF[ routesDF.ROUTE_NUMBER == '107V/R' ]
# this is coming twice under the same depot and then one more time under another depot.

ROUTE_ID ROUTE_NUMBER DEPOT_CODE number_part
9743       6325       107V/R        BGD         107
5918       6353       107V/R        BGD         107
141813     5967       107V/R        HN1         107

## group to see how many id's and depots have the same route_number

In [27]:
def route_grouping(x):
    names = {
        'ROUTE_ID': list(x['ROUTE_ID']) if len(x['ROUTE_ID'])>1 else x['ROUTE_ID'].iloc[0],
        'DEPOT_CODE': list(x['DEPOT_CODE']) if len(x['DEPOT_CODE'])>1 else x['DEPOT_CODE'].iloc[0],
        'count_route_id': x['ROUTE_ID'].count(),
        'count_depot': len(set(x['DEPOT_CODE'])), # length of set, to skip repeating depots
        
        # adding in a column which says if its a number, a word or mixed
        'alphanumeric': 'number' if x.name.isnumeric() else 'word' if x.name[0].isalpha() else 'mixed',
        'number_part' : x['number_part'].iloc[0]
    }
    return pd.Series(names, index=['alphanumeric','number_part','ROUTE_ID','count_route_id','DEPOT_CODE','count_depot'])

routesGroup1 = routesDF.groupby(['ROUTE_NUMBER']).apply(route_grouping).reset_index()
routesGroup1

ROUTE_NUMBER alphanumeric number_part             ROUTE_ID  \
0                 1       number           1                   77   
1                10       number          10                 8026   
2               100       number         100                 7471   
3              100D        mixed         100                24589   
4              100R        mixed         100                 6335   
5            101K/D        mixed         101                28949   
6               102       number         102                 6008   
7          102/253L        mixed         102                11905   
8            102A/G        mixed         102                 6036   
9              102B        mixed         102                 5922   
10        102B/218L        mixed         102                 5924   
11             102C        mixed         102                 6026   
12             102K        mixed         102        [14499, 6015]   
13             102M        mixed         102                 6018   
14             102P        mixed         102                 6048   
15             102W        mixed         102                 6047   
16              103       number         103                 6032   
17             104A        mixed         104                 6014   
18         104A/216        mixed         104                 5946   
19        104M/127K        mixed         104                 5948   
20             104R        mixed         104                 6011   
21        104R/127K        mixed         104                 5982   
22        104R/218L        mixed         104                 5923   
23             104S        mixed         104                 5945   
24              105       number         105                 6038   
25          107J/21        mixed         107                 9360   
26            107JD        mixed         107                 5288   
27            107JS        mixed         107                 5226   
28         107JS-XC        mixed         107                 9672   
29           107V/R        mixed         107   [6325, 6353, 5967]   
..              ...          ...         ...                  ...   
665        ECIL-TPT         word                            10395   
666          GUNTUR         word                   [11609, 10588]   
667          KADAPA         word                             9947   
668             KNL         word                            27009   
669              KP         word                            18909   
670              M1         word                            29219   
671      MARKAPURAM         word                             9648   
672   MGBS-TIRUPATI         word                            11786   
673          MP-NZB         word                            12272   
674         MYP-GDK         word                            15396   
675        MYP-KRMR         word                            15397   
676         MYP-NZB         word                            10022   
677         MYP-VJA         word                             9827   
678        MYP-WGLL         word                            10023   
679             NDL         word                             9825   
680  NIZAMABAD-ARSP         word                            11047   
681  NIZAMABAD-MBRK         word                            11049   
682          ONGOLE         word                             9647   
683              P1         word                            10841   
684      PALAMANERU         word                            14250   
685            PCPL         word                             7427   
686     PULIVENDULA         word                            11608   
687     THADIPATHRI         word                            12478   
688      VIJAYAWADA         word                             9646   
689             VJA         word              [9780, 10027, 9997]   
690        VJA-ATNR         word                             9831   
691  

In [28]:
# sorting by route number
routesGroup2 = routesGroup1.sort_values(['number_part','ROUTE_NUMBER','count_depot'],\
    ascending=[True,True,False])
routesGroup2

ROUTE_NUMBER alphanumeric number_part                ROUTE_ID  \
0                 1       number           1                      77   
195              1B        mixed           1                   14221   
196              1D        mixed           1                    7468   
197          1D/299        mixed           1                    5899   
198         1D/299S        mixed           1                   10036   
199            1D/J        mixed           1                   14955   
200            1D/V        mixed           1                    5928   
201              1J        mixed           1                     138   
202              1L        mixed           1                    6360   
203            1M/D        mixed           1                    6331   
204              1P        mixed           1                      78   
205          1P/25S        mixed           1                    9358   
206              1V        mixed           1                    6082   
207              1Z        mixed           1                     658   
419              2C        mixed           2           [5291, 14054]   
420              2J        mixed           2                     115   
421              2U        mixed           2                   14497   
422              2Z        mixed           2                    5493   
423               3       number           3                    5607   
441              3D        mixed           3                   10154   
442              3H        mixed           3                   10161   
443            3H/N        mixed           3                     574   
444             3HN        mixed           3                   10110   
445              3K        mixed           3  [17, 10109, 575, 5595]   
446          3K/252        mixed           3                   11913   
447             3KL        mixed           3                    9436   
448             3KN        mixed           3                   18418   
449              3M        mixed           3                   10191   
450              3Y        mixed           3                   10158   
549              5G        mixed           5            [5888, 8213]   
..              ...          ...         ...                     ...   
665        ECIL-TPT         word                               10395   
666          GUNTUR         word                      [11609, 10588]   
667          KADAPA         word                                9947   
668             KNL         word                               27009   
669              KP         word                               18909   
670              M1         word                               29219   
671      MARKAPURAM         word                                9648   
672   MGBS-TIRUPATI         word                               11786   
673          MP-NZB         word                               12272   
674         MYP-GDK         word                               15396   
675        MYP-KRMR         word                               15397   
676         MYP-NZB         word                               10022   
677         MYP-VJA         word                                9827   
678        MYP-WGLL         word                               10023   
679             NDL         word                                9825   
680  NIZAMABAD-ARSP         word                               11047   
681  NIZAMABAD-MBRK         word                               11049   
682          ONGOLE         word                                9647   
683              P1         word                               10841   
684      PALAMANERU         word                               14250   
685            PCPL         word                                7427   
686     PULIVENDULA         word                               11608   
687     THADIPATHRI         word                               12478   
688      VIJAYAWADA         word               

In [29]:
routesGroup2.to_csv('route_id_depot_listing.csv',index=False)

In [30]:
save2Excel(routesGroup2, 'Route_id_depot_listing', indexlabel=False)

Existing sheets in TSRTC-analysis.xlsx : ['Stops_Repeating', 'Stops_Grouping', 'ServiceType_Stops']
Sheet Route_id_depot_listing added to TSRTC-analysis.xlsx


In [31]:
'#'*100

'####################################################################################################'

In [32]:
# filtering for getting repeats only, and sort by max repeats first
routesGroup3 = routesGroup2[routesGroup2.count_route_id > 1]\
    .sort_values(['count_route_id','count_depot','number_part','ROUTE_NUMBER'],\
    ascending=[False,False,True,True])
routesGroup3

ROUTE_NUMBER alphanumeric number_part  \
267          219       number         219   
427          300       number         300   
261          218       number         218   
619          90L        mixed          90   
445           3K        mixed           3   
644           9X        mixed           9   
63          113M        mixed         113   
389         288D        mixed         288   
604           8A        mixed           8   
62        113K/L        mixed         113   
91          127K        mixed         127   
182         195W        mixed         195   
208          201       number         201   
246      212/568        mixed         212   
265         218L        mixed         218   
343         253M        mixed         253   
365          280       number         280   
689          VJA         word               
451           40       number          40   
29        107V/R        mixed         107   
419           2C        mixed           2   
549           5G        mixed           5   
551           5K        mixed           5   
574          6NG        mixed           6   
587           7Z        mixed           7   
607         8A/U        mixed           8   
609           8C        mixed           8   
612           8M        mixed           8   
639           9F        mixed           9   
640           9K        mixed           9   
..           ...          ...         ...   
161       187D/V        mixed         187   
163         187P        mixed         187   
166         189M        mixed         189   
218          204       number         204   
249          216       number         216   
256          217       number         217   
258         217A        mixed         217   
262         218C        mixed         218   
263         218D        mixed         218   
272         220J        mixed         220   
273         220K        mixed         220   
279         222A        mixed         222   
280         222L        mixed         222   
288         225L        mixed         225   
289          226       number         226   
324          251       number         251   
346         254K        mixed         254   
362          279       number         279   
367         280B        mixed         280   
368         280E        mixed         280   
381         283S        mixed         283   
399          290       number         290   
428      300/126        mixed         300   
465          458       number         458   
482          478       number         478   
525          532       number         532   
538          568       number         568   
666       GUNTUR         word               
634          95M        mixed          95   
463          455       number         455   

                                              ROUTE_ID  count_route_id  \
267  [9756, 5237, 15388, 9811, 10827, 571, 8134, 81...               9   
427  [6318, 6327, 8477, 5648, 5943, 5783, 5488, 574...               9   
261                [9750, 52, 10144, 5914, 9813, 5567]               6   
619                    [6357, 16290, 5960, 6120, 9354]               5   
445                             [17, 10109, 575, 5595]               4   
644                         [5530, 5601, 14055, 10370]               4   
63                           [5528, 13729, 5577, 6566]               4   
389                          [10385, 5838, 5483, 9047]               4   
604                                [5613, 14056, 8106]               3   
62                                [5546, 10807, 18192]               3   
91                                    [5534, 62, 5587]               3   
182                               [5550, 17913, 10829]               3   
208                                 [6320, 5985, 6110]               3   
246                               [16311, 15296, 8138]               3   
265                                [9777, 5541, 14498]               3   
343                          

In [33]:
# check if in this there are repeating depots, ie if a route is repeating in the same depot also
# routesGroup3['same_depot_repeat'] = routesGroup3.apply( lambda row: row['count_route_id'] != row['count_depot'], axis=1)
# using .assign() . don't have to specify axis there.
# from https://pandas.pydata.org/pandas-docs/version/0.22/generated/pandas.DataFrame.assign.html
routesGroup3 = routesGroup3.assign(same_depot_repeat = lambda row: row['count_route_id'] != row['count_depot'] )
routesGroup3[ routesGroup3['same_depot_repeat'] ]

ROUTE_NUMBER alphanumeric number_part  \
267          219       number         219   
427          300       number         300   
451           40       number          40   
29        107V/R        mixed         107   
634          95M        mixed          95   
463          455       number         455   

                                              ROUTE_ID  count_route_id  \
267  [9756, 5237, 15388, 9811, 10827, 571, 8134, 81...               9   
427  [6318, 6327, 8477, 5648, 5943, 5783, 5488, 574...               9   
451                               [18296, 18306, 5596]               3   
29                                  [6325, 6353, 5967]               3   
634                                       [5576, 5749]               2   
463                                       [5500, 5554]               2   

                                        DEPOT_CODE  count_depot  \
267  [BHL, CNT, HPT, MI1, MI2, MS1, RN1, RN1, RN2]            8   
427  [BGD, BGD, CCL, FMA, HN1, MPM, RJN, RJN, UPL]            7   
451                                [MS1, MS1, MS2]            2   
29                                 [BGD, BGD, HN1]            2   
634                                     [RJN, RJN]            1   
463                                     [RJN, RJN]            1   

     same_depot_repeat  
267               True  
427               True  
451               True  
29                True  
634               True  
463               True

In [34]:
routesGroup3.columns

Index(['ROUTE_NUMBER', 'alphanumeric', 'number_part', 'ROUTE_ID',
       'count_route_id', 'DEPOT_CODE', 'count_depot', 'same_depot_repeat'],
      dtype='object')

In [35]:
# setting in proper order
routesGroup4 = routesGroup3[['ROUTE_NUMBER', 'DEPOT_CODE', 'count_depot','same_depot_repeat', 'ROUTE_ID',
       'count_route_id', 'alphanumeric', 'number_part']]

In [36]:
routesGroup4.to_csv('routes_repeating.csv',index=False)

In [37]:
save2Excel(routesGroup4,'Routes_repeating',indexlabel=False)

Existing sheets in TSRTC-analysis.xlsx : ['Stops_Repeating', 'Stops_Grouping', 'ServiceType_Stops', 'Route_id_depot_listing']
Sheet Routes_repeating added to TSRTC-analysis.xlsx


In [44]:
save2Excel(routesGroup4[routesGroup4.same_depot_repeat],'Routes_sameDepot',indexlabel=False)

Existing sheets in TSRTC-analysis.xlsx : ['Stops_Repeating', 'Stops_Grouping', 'ServiceType_Stops', 'Route_id_depot_listing', 'Routes_repeating']
Sheet Routes_sameDepot added to TSRTC-analysis.xlsx


In [38]:
'#'*100

'####################################################################################################'

In [39]:
## see how many routes are numbers, word, mixed

In [40]:
routesGroup2.groupby('alphanumeric').alphanumeric.count()

alphanumeric
mixed     528
number    121
word       46
Name: alphanumeric, dtype: int64

In [41]:
#routesGroup2[ routesGroup2.alphanumeric == 'word']

In [42]:
'#'*100

'####################################################################################################'

## Writing the grouped analysis DF's to excel file

### > saved grouping analysis tables to a TSRTC-analysis.xlsx file

In [45]:
'#'*100

'####################################################################################################'